In [21]:
# Importando a biblioteca necessária
import pandas as pd

# 1. Carregar o dataset com delimitador e codificação corretos, e especificando os tipos de dados para as colunas
dataset = pd.read_csv(
    'DataSet.dsv', 
    delimiter=';', 
    encoding='latin1', 
    dtype={'CO_PA_AUTORIZ': str, 
           'CO_PA_CNSPAC': str,
           'CO_PA_PROC_ID': str,
           'CO_PA_MVM': str}
)

# 2. Filtrar para pacientes identificados
pacientes_identificados = dataset[dataset['CO_PA_CNSPAC'] != '000000000000000']

# 3. Filtrar os registros pelos códigos de procedimentos
biopsia_prostata = pacientes_identificados[pacientes_identificados['CO_PA_PROC_ID'] == '0201010410']
exame_anatomopatologico = pacientes_identificados[pacientes_identificados['CO_PA_PROC_ID'] == '0203020030']

# 4. Encontrar pacientes que fizeram ambos os procedimentos
pacientes_both = pd.merge(
    biopsia_prostata[['CO_PA_CNSPAC', 'CO_PA_MVM', 'NU_PA_QTDAPR', 'NU_PA_VALAPR']],
    exame_anatomopatologico[['CO_PA_CNSPAC', 'CO_PA_MVM', 'NU_PA_QTDAPR', 'NU_PA_VALAPR']],
    on='CO_PA_CNSPAC',
    suffixes=('_biopsia', '_anatomopatologico')
)

# 5. Função para limpar e converter strings de valores monetários
def limpar_e_converter(valor):
    if isinstance(valor, str):
        valor = valor.replace('.', '').replace(',', '.')
    try:
        return float(valor)
    except ValueError:
        return 0.0  # Retornar 0.0 se a conversão falhar

# 6. Aplicar a função de limpeza e conversão nas colunas relevantes
pacientes_both['NU_PA_QTDAPR_biopsia'] = pacientes_both['NU_PA_QTDAPR_biopsia'].apply(limpar_e_converter)
pacientes_both['NU_PA_VALAPR_biopsia'] = pacientes_both['NU_PA_VALAPR_biopsia'].apply(limpar_e_converter)
pacientes_both['NU_PA_QTDAPR_anatomopatologico'] = pacientes_both['NU_PA_QTDAPR_anatomopatologico'].apply(limpar_e_converter)
pacientes_both['NU_PA_VALAPR_anatomopatologico'] = pacientes_both['NU_PA_VALAPR_anatomopatologico'].apply(limpar_e_converter)

# 7. Calcular a soma das quantidades e valores aprovados
pacientes_both['SOMA_NU_PA_QTDAPR'] = pacientes_both['NU_PA_QTDAPR_biopsia'] + pacientes_both['NU_PA_QTDAPR_anatomopatologico']
pacientes_both['SOMA_NU_PA_VALAPR'] = pacientes_both['NU_PA_VALAPR_biopsia'] + pacientes_both['NU_PA_VALAPR_anatomopatologico']

# 8. Identificar inconsistências na ordem dos procedimentos
pacientes_inconsistentes = pacientes_both[pacientes_both['CO_PA_MVM_anatomopatologico'] < pacientes_both['CO_PA_MVM_biopsia']]

# 9. Contar o número de pacientes identificados que realizaram ambos os procedimentos corretamente e com inconsistência
num_pacientes_both = pacientes_both['CO_PA_CNSPAC'].nunique()
num_pacientes_inconsistentes = pacientes_inconsistentes['CO_PA_CNSPAC'].nunique()

# 10. Identificar os meses em que cada paciente realizou cada exame (para os procedimentos consistentes)
meses_procedimentos = pacientes_both.groupby('CO_PA_CNSPAC')[['CO_PA_MVM_biopsia', 'CO_PA_MVM_anatomopatologico']].agg(list)

# 11. Exibir o resultado
print(f"Número de pacientes identificados que realizaram ambos os procedimentos: {num_pacientes_both}")
print(f"Número de pacientes com inconsistência na ordem dos procedimentos: {num_pacientes_inconsistentes}")
print("Meses em que cada paciente realizou a biópsia e o exame anatomopatológico:")
print(meses_procedimentos)

# 12. Exibir soma detalhada para cada paciente
resultado_final = pacientes_both[['CO_PA_CNSPAC', 'CO_PA_MVM_biopsia', 'SOMA_NU_PA_QTDAPR', 'SOMA_NU_PA_VALAPR',
                                   'NU_PA_QTDAPR_biopsia', 'NU_PA_VALAPR_biopsia', 
                                   'NU_PA_QTDAPR_anatomopatologico', 'NU_PA_VALAPR_anatomopatologico']]

print("\nSoma detalhada para cada paciente:")
print(resultado_final)

# 13. Exportar os resultados para Excel
meses_procedimentos.to_excel('meses_procedimentos.xlsx', index=True)
resultado_final.to_excel('resultado_final.xlsx', index=False)
pacientes_inconsistentes.to_excel('pacientes_inconsistentes.xlsx', index=False)

print("\nResultados exportados para Excel com sucesso!")


Número de pacientes identificados que realizaram ambos os procedimentos: 614
Número de pacientes com inconsistência na ordem dos procedimentos: 24
Meses em que cada paciente realizou a biópsia e o exame anatomopatológico:
                CO_PA_MVM_biopsia CO_PA_MVM_anatomopatologico
CO_PA_CNSPAC                                                 
103845770990000          [202307]                    [202307]
103878406880000          [202308]                    [202308]
103888879980002          [202310]                    [202310]
104124408970008          [202308]                    [202308]
104821833460008          [202312]                    [202312]
...                           ...                         ...
898003963078989          [202309]                    [202309]
898004030513974          [202302]                    [202302]
898004231319172          [202307]                    [202307]
898004850325558          [202302]                    [202302]
898050097438997          [202302] 

CO_PA_CNSPAC CO_PA_MVM_biopsia CO_PA_MVM_anatomopatologico
0    801440468394627            202303                      202302
1    801440468394627            202301                      202302
2    801434179238999            202303                      202303
3    801434186680219            202303                      202304
4    801434186680219            202304                      202304
..               ...               ...                         ...
683  898001402582597            202301                      202301
684  801440414717940            202301                      202301
685  898000634297203            202301                      202301
686  801440472859132            202308                      202308
687  801440410736398            202308                      202308

[688 rows x 3 columns]